In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [2]:
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr):
    return [sentiment_vector_to_emoji(s) for s in sent_arr]

In [3]:
SINGLE_LABEL = True

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [4]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [5]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [6]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [12]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [13]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [14]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("(<EMOJI>|<USER>|<HASHTAG>)","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* defining different criterias for choosing a single emoji (currently `latest` is used)

In [10]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

* convert all emojis to a sentiment vector

In [11]:
labels = emoji2sent([latest(e) for e in emojis])


In [12]:
len(labels)

68733

In [13]:
wrong_labels = np.isnan(np.linalg.norm(labels, axis=1))

* remove all data we have no label for

In [14]:
labels = labels[np.invert(wrong_labels)]
plain_text = plain_text[np.invert(wrong_labels)]
emojis = emojis[np.invert(wrong_labels)]

In [15]:
print(len(labels), len(emojis), len(plain_text))

33368 33368 33368


* generate weights:

In [16]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* generating train and test set:

In [17]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [38]:
#y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in sent2emoji(y1)])

In [39]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [40]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

In [53]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='categorical_crossentropy',
              optimizer='sgd',
              metrics=['accuracy'],)
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2, epochs=1)#, sample_weight=y1_weights[:max_size])
    
    return clf

In [54]:
clf = train(max_size=10000,layers=[(6200, 'relu'),(y1[0].shape[0],'softmax')])

Train on 24024 samples, validate on 6007 samples
Epoch 1/1
 8576/24024 [=========>....................] - ETA: 10:31 - loss: 1.0637 - acc: 0.7273

KeyboardInterrupt: 

In [43]:
X1

61236            <USER> Look at you!! Smart and beautiful 
66498                                        Missing home 
3920                                               Lmfao  
10415                                      thats true..   
61218                                       <USER> wrong  
49421          Lmao  no o, it's almost 8pm. Cheating time 
44693                                        <USER> noted 
21987    Lol the stupid question mark boxes ruined my t...
6458                                She look just like u  
18291    <USER> Popeyes chicken with a KFC biscuit though 
21859    Still so unreal that my man an i have our own ...
103      That’s what I said when I seen it  that’s craz...
68215                    dnt really knw what jst happened 
66229               im so tired but not after seeing him  
58987                                  As if I don't know 
1272     <USER> Hahaha was it big? I’m not afraid of sp...
57222    Me seeing pics of my abusive ex with a kitten:.

* make a prediction and store it in a csv file:

In [44]:
pred = clf.predict(vectorizer.transform(Xt1))

In [45]:
pred

array([[0.45662233, 0.2710931 , 0.27228457],
       [0.4544683 , 0.27005136, 0.2754803 ],
       [0.45572498, 0.2714926 , 0.27278242],
       ...,
       [0.4522461 , 0.27333662, 0.2744173 ],
       [0.45729154, 0.26964816, 0.27306038],
       [0.45031306, 0.2748751 , 0.2748118 ]], dtype=float32)

In [49]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 
                         'teacher': sent2emoji(yt1),
                         'teacher_sentiment': yt1.tolist(),
                         'predict': sent2emoji(pred),
                         'predicted_sentiment': pred.tolist()})

In [50]:
display(testlist)


predict                                predicted_sentiment teacher  \
7618        😬  [0.45662233233451843, 0.27109310030937195, 0.2...       😒   
6910        😱  [0.454468309879303, 0.27005136013031006, 0.275...       😂   
35783       😬  [0.4557249844074249, 0.271492600440979, 0.2727...       😭   
15623       😬  [0.4551065266132355, 0.27315083146095276, 0.27...       😅   
12023       😱  [0.44956669211387634, 0.2718639373779297, 0.27...       😭   
15763       😱  [0.4546020030975342, 0.27004513144493103, 0.27...       😂   
57240       😱  [0.4514758884906769, 0.2734237313270569, 0.275...       😎   
2418        😬  [0.4555293321609497, 0.2700120508670807, 0.274...       😂   
66384       😬  [0.4541899561882019, 0.27133306860923767, 0.27...       😍   
44639       😬  [0.45672306418418884, 0.2679496109485626, 0.27...       😂   
54463       😱  [0.45094504952430725, 0.2715355157852173, 0.27...       🙌   
38407       😱  [0.45006927847862244, 0.2722932994365692, 0.27...       😎   
31342       😬  [0.45655250549316406, 0.26978597044944763, 0.2...       😄   
41255       😱  [0.45397621393203735, 0.27026963233947754, 0.2...       😂   
19686       😱  [0.4501204788684845, 0.27288398146629333, 0.27...       😭   
67193       😱  [0.45182353258132935, 0.2724774479866028, 0.27...       😂   
40650       😱  [0.45002350211143494, 0.2710316777229309, 0.27...       😇   
64416       😱  [0.45193251967430115, 0.2698008418083191, 0.27...       😊   
19525       😱  [0.45155930519104004, 0.27194666862487793, 0.2...       🙆   
39024       😱  [0.4556638300418854, 0.26780301332473755, 0.27...       😂   
35342       😱  [0.452972412109375, 0.27151480317115784, 0.275...       😫   
9715        😱  [0.4522416293621063, 0.2719023823738098, 0.275...       😇   
40490       😬  [0.4545004665851593, 0.27230802178382874, 0.27...       😮   
22064       😬  [0.4601033926010132, 0.2683771550655365, 0.271...       😍   
53563       😱  [0.45222631096839905, 0.2727421224117279, 0.27...       😄   
67332       😬  [0.45455402135849, 0.27052536606788635, 0.2749...       😪   
15404       😱  [0.45141908526420593, 0.2713443338871002, 0.27...       😕   
30130       😬  [0.4556472599506378, 0.2695685029029846, 0.274...       😳   
37242       😬  [0.4568144977092743, 0.27149033546447754, 0.27...       😂   
30533       😬  [0.45350709557533264, 0.27462711930274963, 0.2...       😂   
...       ...                                                ...     ...   
16955       😱  [0.45130616426467896, 0.2745077311992645, 0.27...       🙏   
36805       😬  [0.4585663378238678, 0.26974013447761536, 0.27...       😂   
56326       😱  [0.45519477128982544, 0.2686183452606201, 0.27...       😢   
40306       😱  [0.449861079454422, 0.2748417556285858, 0.2752...       😍   
51333       😱  [0.4518674910068512, 0.2723572850227356, 0.275...       😌   
42339       😬  [0.4573005437850952, 0.2696344256401062, 0.273...       😔   
7644        😱  [0.4539974331855774, 0.2710561156272888, 0.274...       😧   
13953       😱  [0.4520905911922455, 0.27237412333488464, 0.27...       😐   
26460       😱  [0.4516184329986572, 0.2706548869609833, 0.277...       😛   
31571       😱  [0.4516292214393616, 0.2722293734550476, 0.276...       😒   
9536        😱  [0.45403042435646057, 0.27084800601005554, 0.2...       😭   
19571       😱  [0.45092839002609253, 0.273369699716568, 0.275...       😡   
35934       😱  [0.45402011275291443, 0.2693026065826416, 0.27...       😂   
4605        😬  [0.45629507303237915, 0.2681595981121063, 0.27...       😂   
1913        😬  [0.45600560307502747, 0.26834917068481445, 0.2...       😭   
11827       😬  [0.45951539278030396, 0.26939070224761963, 0.2...       😄   
15181       😬  [0.4616319239139557, 0.2665380537509918, 0.271...       😂   
32869       😬  [0.45471736788749695, 0.27229392528533936, 0.2...       😹   
40784       😬  [0.45305681228637695, 0.2729623019695282, 0.27...       😻   
18611       😱  [0.4504826068878174, 0.27414649724960327, 0.27...       😂   
28341       😱  [0.45293256640434265, 0.271566867828369

In [61]:
testlist.to_csv('test.csv')

* a simple output widget for testing:

In [63]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        display(Markdown("# " + str(sent2emoji(pred))))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

VBox(children=(Button(description='get smiley', icon='check', style=ButtonStyle(), tooltip='Click me'), Output()))

In [ ]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)